In [1]:
import numpy as np
from itertools import product
import math
import random
import copy

According to Hinton's "A Practical Guide to Training Restricted Boltzmann Machines"

Initialize J matrix to zero mean and 0.01 sd. The diagonal will be 0.

Initizlize bias b_i  of visible unit i to log[pi/(1−pi)]

#### ISING MODEL

In [32]:
class IsingModel:
    def __init__(self, lr=0.01):
        self.lr = lr
        
        # Possible values the spins can take
        self.spin_values = [-1,1]
        self.gaussian_scale = 0.01
        
    
    def fit_activations(self, activations_list):
        
        # Create a ndarray from the data
        self.data_activations_matrix = np.array(activations_list)
        # Calculate the shape of the matrix and save useful variables
        self.num_spins = self.data_activations_matrix.shape[1]
        self.num_samples_data = self.data_activations_matrix.shape[0]
        
        # Calculate the true data expectations
        # Calculate the mean
        self.data_mean = np.mean(self.data_activations_matrix, axis=0)
        
        # Calculate the correlation
        self.data_correlation = self.calculate_corr(self.data_activations_matrix)
        
        #Create random H and J matrices
        self.create_H_J()
        
         
    def fit_m_c(self, m, C):
        self.data_mean = m
        self.data_correlation = C
    
    def create_H_J(self, gaussian_scale = None):
        if gaussian_scale is None:
            gaussian_scale = self.gaussian_scale
            
        # Calculate the initial J matrix. Fill only the upper diagonal
        # Filling with Normal(0, 0.01)
        np.random.seed(3)
        self.J = np.random.normal(loc=0.0, scale=gaussian_scale, size=(self.num_spins, self.num_spins))
        self.lind = np.tril_indices_from(self.J)
        self.J[self.lind]=0
                
        # Calculate the initial H vector, each entry proportional to its probability (according to Hinton)
        #self.H = np.sum(self.data_activations_matrix, axis=0)/ float(self.num_samples_data)
        # Try with random H
        self.H = np.random.normal(loc=0.0, scale=gaussian_scale, size=self.num_spins)
    
    def set_H_J(self):
        self.H = H
        self.J = J        
        
    # Train the exact model
    def train(self, max_epochs = 500):
        
        totalParamVariation = math.inf
        stopCondition = 0.0001
        
        epoch = 1
        
        while totalParamVariation > stopCondition and epoch < max_epochs:
            # Calculate P(sigma) for every possible combination in the model

            prob_dict = {}
            for sigma in product(self.spin_values, repeat=self.num_spins):
                prob_dict[sigma] = math.exp(-self.calculate_energy(sigma))

            # Compute the statistics
            model_mean, model_correlation = self.get_statistics(prob_dict)

            # Calculate the step size for every J_{ij}
            stepJ = self.lr * (self.data_correlation - model_correlation)
            # Take the step
            oldJ = copy.deepcopy(self.J)
            self.J = self.J + stepJ
            self.J[self.lind]=0

            # Calculate the step size for every H_{i}
            stepH = self.lr * (self.data_mean - model_mean)
            # Calculate the variation of J for the termination condition
            # Take the step
            oldH = copy.deepcopy(self.H)
            self.H = self.H + stepH
            
            diffH = np.sum(np.absolute(self.H - oldH))
            diffJ = np.sum(np.sum(np.absolute(self.J - oldJ)))
            totalParamVariation = diffJ + diffH
            
            if epoch%100 == 0:
                print('Epoch', epoch, 'TotalParamVariation', round(totalParamVariation, 8))
                print(model_correlation, 'Corr Model')
                print(self.data_correlation, 'Corr Data')

                print(model_mean, 'Average Model')
                print(self.data_mean, 'Average Data')
                print()
            
            epoch += 1
            
        print('Final stats. TotalParamVariation', round(totalParamVariation, 8))
        print('Total epochs', epoch-1)
        print(model_correlation, 'C Model')
        print(self.data_correlation, 'C Data')

        print(model_mean, 'Average Model')
        print(self.data_mean, 'Average Data')
        print()

        print(self.H, 'H')
        print(self.J, 'J')

    # Calculate the energy of the model's parameters given a sigma state
    def calculate_energy(self, sigma):
        energy = 0
        for i in range(0, self.num_spins):
            for j in range(i+1, self.num_spins):
                energy += sigma[i]*sigma[j]*self.J[i][j]

        for i in range(0, self.num_spins):
            energy += sigma[i]*self.H[i]

        return - energy
    
    def get_delta_energy(self, i):
        #delta_energy = 2*(self.H[spin_to_flip]*self.sigma[spin_to_flip])
        
        delta_energy= 2 * (self.H[i]*self.sigma[i] \
                           + self.sigma[i] * np.dot(self.J[i, :], self.sigma) \
                           + self.sigma[i] * np.dot(self.J[:, i], self.sigma))
        
        return delta_energy

    # Calculates the correlation of a list of activations
    def calculate_corr(self, activations_matrix):
        num_samples_data = activations_matrix.shape[0]
        
        corr_matrix = np.zeros((self.num_spins, self.num_spins))
        for sigma in activations_matrix:
            # Calculate \sigma_i * \sigma_j
            for i in range(0, self.num_spins):
                for j in range(i+1, self.num_spins):
                    corr_matrix[i][j] += sigma[i]*sigma[j]
        corr_matrix = corr_matrix / float(num_samples_data)
        
        return corr_matrix
    
    def get_statistics(self, states_dict):
        
        # Calculate the partition function
        Z = sum(states_dict.values())
        normalized_dict = {sigma: u_prob / Z for sigma, u_prob in states_dict.items()}
        
        # Returns the magnetization and correlation from a dictionary of activations {sigma, prob}
        magnetization =  np.zeros(self.num_spins)
        corr_matrix = np.zeros((self.num_spins,self.num_spins))
        # Calculate the expectation
        for sigma, prob in normalized_dict.items():
            magnetization += np.dot(sigma, prob)
            for i in range(0, self.num_spins):
                for j in range(i+1, self.num_spins):
                    if i == 0 and j == 2:
                    corr_matrix[i][j] += sigma[i]*sigma[j]*prob
                    
        return magnetization, corr_matrix
    
    def metropolis_step(self):
        # Randomly select a spin (now it can only select 0)
        spin_to_flip = np.random.randint(self.num_spins)
        delta_energy = self.get_delta_energy(spin_to_flip)

        p = math.exp(-delta_energy)
        r = random.random()

        #print(delta_energy, r, p)
        if delta_energy <= 0 or r<=p:
            self.sigma[spin_to_flip] = -self.sigma[spin_to_flip]

    def metropolis_simulation(self, max_steps, initial_burn_in_len=0, inter_burn_in=0):
        # Generate a random initial spin configuration
        self.sigma = random.choices(self.spin_values, k=self.num_spins)        
        
        # Create a dictionary to count the frequencies
        samples_dict = {}
        for i in range(0, max_steps):
            # Take a metropolis step
            self.metropolis_step()
            
            # Save the state if the burn-in phase has passed
            if i >= initial_burn_in_len and (i%inter_burn_in)==0:
                if not tuple(copy.deepcopy(self.sigma)) in samples_dict: # If the state is new, create an entry
                    samples_dict[tuple(copy.deepcopy(self.sigma))] = 1
                else: # If the state already appeared, add one
                    samples_dict[tuple(copy.deepcopy(self.sigma))] += 1
                                                 
        return samples_dict
    
    def train_metropolis(self, max_epochs = 300, simulation_len = 100, burn_in_len=0, inter_burn_in=0):
        random.seed(3)
        totalParamVariation = math.inf
        stopCondition = 0.0003
        
        epoch = 1
        
        while totalParamVariation > stopCondition and epoch < max_epochs:

            samples_dict = self.metropolis_simulation(simulation_len, burn_in_len, inter_burn_in)
        
            # Calculate the data expectations        
            model_mean, model_correlation = self.get_statistics(samples_dict)
            
            # Calculate the step size for every J_{ij}
            stepJ = self.lr * (self.data_correlation - model_correlation)
            oldJ = copy.deepcopy(self.J)
            # Take the step
            self.J = self.J + stepJ
            self.J[self.lind]=0
            
            # Calculate the step size for every H_{i}
            stepH = self.lr * (self.data_mean - model_mean)
            # Take the step
            oldH = copy.deepcopy(self.H)
            self.H = self.H + stepH
            
            # Calculate the variation of J and H for the termination condition
            diffH = np.sum(np.absolute(self.H - oldH))
            diffJ = np.sum(np.sum(np.absolute(self.J - oldJ)))
            totalParamVariation = diffJ + diffH
            
            if epoch%50 == 0 or epoch == max_epochs-1:
                print('Epoch', epoch, 'TotalParamVariation', round(totalParamVariation, 8))
                print(model_correlation, 'Corr Model')
                print(self.data_correlation, 'Corr Data')

                print(model_mean, 'Average Model')
                print(self.data_mean, 'Average Data')
                print()
                
            epoch +=1
            
        print('Final stats. TotalParamVariation', round(totalParamVariation, 8))
        print('Total epochs', epoch-1)
        print(model_correlation, 'C Model')
        print(self.data_correlation, 'C Data')

        print(model_mean, 'Average Model')
        print(self.data_mean, 'Average Data')
        print()

        
        print(self.H, 'H')
        print(self.J, 'J')
    
    def create_initial_conditions(self, _num_spins, _num_runs, _simulation_len, _burn_in_len, _inter_burn_in):
        self.num_spins = _num_spins
        
        #Create random H and J matrices
        self.create_H_J()
        
        num_runs = _num_runs
        model_mean_array = np.empty((0,self. num_spins))
        model_correlation_array = np.empty((self.num_spins, self.num_spins, 0))
        for i in range(0,num_runs):
            samples_dict = self.metropolis_simulation(_simulation_len, _burn_in_len, _inter_burn_in)
        
            model_mean, model_correlation = self.get_statistics(samples_dict)
            model_mean_array = np.append(model_mean_array, model_mean.reshape(1, self.num_spins), axis=0)
            model_correlation_array = np.append(model_correlation_array, np.atleast_3d(model_correlation), axis=2)
            
        model_mean = np.mean(model_mean_array, axis=0)
        model_mean_std = np.std(model_mean_array, axis=0)
        model_correlation = np.mean(model_correlation_array, axis=2)
        model_correlation_std = np.std(model_correlation_array, axis=2)

        
        print(self.H, 'iniH')
        print(self.J, 'iniJ')
        
        print(model_mean, 'Mean Data')
        print(model_mean_std, 'Std Data')
        print(model_correlation, 'Corr Data')
        print(model_correlation_std, 'Corr STD')
         
        
        return self.H, self.J, model_mean, model_correlation
        
    

In [33]:
activations_list = [[1,-1,1,-1], [1,-1,1,-1], [-1,1,-1,-1], [-1,1,1,1], [1,1,1,-1], [-1,-1,1,1], [1,-1,-1,1], [1,-1,1,1]]
s_ising = IsingModel(lr=0.01)
s_ising.fit_activations(activations_list)

In [34]:
s_ising.train(10000)

0 2 0.06313227465359277
0 2 0.0637728907632631
0 2 -0.06323841218969048
0 2 -0.06618096388259993
0 2 0.06154491434632917
0 2 0.060629602454756445
0 2 -0.0614446853522992
0 2 -0.06271108839823117
0 2 -0.06413143387145917
0 2 -0.06012892403988855
0 2 0.06448768735138821
0 2 0.06264072127848772
0 2 -0.06362014246313473
0 2 -0.05817213487015
0 2 0.06376217501348015
0 2 0.06040194907124923
[[ 0.          0.00456189  0.00074443 -0.01859197]
 [ 0.          0.         -0.00102916 -0.00619083]
 [ 0.          0.          0.          0.00872698]
 [ 0.          0.          0.          0.        ]]
0 2 0.06217679621136838
0 2 0.06343217968891575
0 2 -0.06290563824247945
0 2 -0.06646403896384821
0 2 0.06154522983164334
0 2 0.060638461810296786
0 2 -0.061445940683335934
0 2 -0.06269932094280534
0 2 -0.06410516050924031
0 2 -0.06014259093257894
0 2 0.06575981308635714
0 2 0.06389480856913031
0 2 -0.06328151449973815
0 2 -0.0573374652147035
0 2 0.06405927355605373
0 2 0.06011176725750456
[[ 0.         

0 2 -0.06081866090156905
0 2 -0.06145104844016831
0 2 -0.05860857938631108
0 2 0.10576555078163599
0 2 0.10362766962734514
0 2 -0.053369623122321956
0 2 -0.03775997697739252
0 2 0.07026405202794568
0 2 0.051070531188130486
[[ 0.         -0.13765162  0.08609953 -0.07263514]
 [ 0.          0.         -0.08824796 -0.06241705]
 [ 0.          0.          0.          0.00482471]
 [ 0.          0.          0.          0.        ]]
0 2 0.03968703613589377
0 2 0.05323281267928604
0 2 -0.05248640540503153
0 2 -0.07230916770118766
0 2 0.059574557619039674
0 2 0.05883538650965367
0 2 -0.0598788135172755
0 2 -0.0607388767255865
0 2 -0.06132857707850218
0 2 -0.05851748546622532
0 2 0.10699476116392702
0 2 0.10485787833759082
0 2 -0.053085987036288904
0 2 -0.03729492187556635
0 2 0.0703872046573349
0 2 0.05079012809161008
[[ 0.         -0.14145267  0.08871953 -0.07382555]
 [ 0.          0.         -0.09087813 -0.06368781]
 [ 0.          0.          0.          0.00474442]
 [ 0.          0.          0

0 2 -0.05775479137017639
0 2 -0.055689189755932074
0 2 0.1374073639941259
0 2 0.13549286928596946
0 2 -0.046371080182081637
0 2 -0.02716435447203025
0 2 0.07278659197856668
0 2 0.04360407855524265
[[ 0.         -0.23176571  0.15371135 -0.09985205]
 [ 0.          0.         -0.15574983 -0.09204358]
 [ 0.          0.          0.          0.00317332]
 [ 0.          0.          0.          0.        ]]
0 2 0.02831827054631659
0 2 0.04634411990779819
0 2 -0.044451159051475404
0 2 -0.07438398267252191
0 2 0.05643499453728267
0 2 0.05575729707592198
0 2 -0.05822503267368829
0 2 -0.05882086294019142
0 2 -0.057630807629191864
0 2 -0.055587279125038504
0 2 0.13833204937563187
0 2 0.13643064979394706
0 2 -0.04617450542352087
0 2 -0.026887367053960012
0 2 0.07284759999353803
0 2 0.043374022199975104
[[ 0.         -0.23443795  0.15567801 -0.10058245]
 [ 0.          0.         -0.15770401 -0.09285633]
 [ 0.          0.          0.          0.00313619]
 [ 0.          0.          0.          0.       

0 2 0.07436073482006829
0 2 0.037506649331630525
[[ 0.         -0.29776621  0.20162057 -0.11825921]
 [ 0.          0.         -0.2032232  -0.11273628]
 [ 0.          0.          0.          0.0023872 ]
 [ 0.          0.          0.          0.        ]]
0 2 0.021337677187018653
0 2 0.04164695254808204
0 2 -0.038020004797557704
0 2 -0.07563100027902352
0 2 0.05350785860950347
0 2 0.052872164631233974
0 2 -0.05776532478323741
0 2 -0.058173919986347716
0 2 -0.05431142959787317
0 2 -0.052808438287581166
0 2 0.16088544255856413
0 2 0.15943381146631963
0 2 -0.04145864159294437
0 2 -0.020408006814825505
0 2 0.0744089549365634
0 2 0.037330371923324245
[[ 0.         -0.29951678  0.20284647 -0.11877701]
 [ 0.          0.         -0.20443386 -0.11332197]
 [ 0.          0.          0.          0.00236942]
 [ 0.          0.          0.          0.        ]]
0 2 0.02115890657370113
0 2 0.04152468042087187
0 2 -0.03783553308976065
0 2 -0.07566993545961247
0 2 0.05342253231816049
0 2 0.052788174100497

0 2 -0.050884300312068295
0 2 0.1739365348832579
0 2 0.172871423195552
0 2 -0.03872958120260784
0 2 -0.01666155640486245
0 2 0.07571866764708153
0 2 0.03312133622583798
[[ 0.         -0.33838683  0.2285817  -0.13130561]
 [ 0.          0.         -0.22977469 -0.1274476 ]
 [ 0.          0.          0.          0.00199051]
 [ 0.          0.          0.          0.        ]]
0 2 0.017214761697255724
0 2 0.038849057539193516
0 2 -0.03345280723454483
0 2 -0.07675551334589999
0 2 0.05142438702090059
0 2 0.05082672593368542
0 2 -0.058425469119649284
0 2 -0.05871144372623896
0 2 -0.051986398672352184
0 2 -0.05082326214436234
0 2 0.1743169044961638
0 2 0.1732646037709792
0 2 -0.03864868325371609
0 2 -0.016548210841241754
0 2 0.07576803185240939
0 2 0.03298373935140703
[[ 0.         -0.33955839  0.22929642 -0.13172552]
 [ 0.          0.         -0.23047567 -0.12791802]
 [ 0.          0.          0.          0.00197906]
 [ 0.          0.          0.          0.        ]]
0 2 0.017095700205520942
0

...

0 2 0.09150341797901726
0 2 0.0009328420928240742
[[ 0.00000000e+00 -4.96616710e-01  2.50004112e-01 -2.46611635e-01]
 [ 0.00000000e+00  0.00000000e+00 -2.50004109e-01 -2.46611635e-01]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  1.16994414e-09]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00]]
0 2 0.0003371148690033093
0 2 0.033072417367882925
0 2 -0.0009327161061721348
0 2 -0.0915034608655677
0 2 0.04579541986978181
0 2 0.04579541857228877
0 2 -0.07878069917601108
0 2 -0.0787806991760111
0 2 -0.04579541986978182
0 2 -0.04579541857228876
0 2 0.2037827539207741
0 2 0.2037827539207741
0 2 -0.03307241590691375
0 2 -0.0003371148350087802
0 2 0.09150346086556765
0 2 0.0009327161061721348
[[ 0.00000000e+00 -4.96617166e-01  2.50004111e-01 -2.46612093e-01]
 [ 0.00000000e+00  0.00000000e+00 -2.50004108e-01 -2.46612093e-01]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  1.16801153e-09]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00]]
0 2 0.000337069

0 2 0.033072851165551205
0 2 -0.0009289522446992163
0 2 -0.09150474209056696
0 2 0.04579588172112044
0 2 0.045795880486288514
0 2 -0.07878195037898227
0 2 -0.07878195037898227
0 2 -0.045795881721120466
0 2 -0.045795880486288514
0 2 0.20378398843851675
0 2 0.2037839884385167
0 2 -0.03307284977516374
0 2 -0.00033575415335762587
0 2 0.09150474209056696
0 2 0.0009289522446992163
[[ 0.00000000e+00 -4.96630804e-01  2.50004078e-01 -2.46625772e-01]
 [ 0.00000000e+00  0.00000000e+00 -2.50004075e-01 -2.46625772e-01]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  1.11149795e-09]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00]]
0 2 0.0003357090183448038
0 2 0.03307286556526122
0 2 -0.0009288273050005221
0 2 -0.09150478461978738
0 2 0.04579589705220558
0 2 0.045795895819409294
0 2 -0.07878199191162955
0 2 -0.07878199191162955
0 2 -0.04579589705220558
0 2 -0.04579589581940931
0 2 0.20378402941849086
0 2 0.20378402941849097
0 2 -0.03307286417716672
0 2 -0.000335708986180685
0 2

0 2 -0.0003344940428669401
0 2 0.09150592859482057
0 2 0.0009254665729688393
[[ 0.00000000e+00 -4.96643434e-01  2.50004047e-01 -2.46638440e-01]
 [ 0.00000000e+00  0.00000000e+00 -2.50004044e-01 -2.46638440e-01]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  1.06122627e-09]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00]]
0 2 0.0003344492441827888
0 2 0.033073267192395193
0 2 -0.0009253425677392942
0 2 -0.0915059708051126
0 2 0.045796324660434824
0 2 0.0457963234832926
0 2 -0.07878315030104449
0 2 -0.07878315030104445
0 2 -0.045796324660434824
0 2 -0.04579632348329262
0 2 0.20378517242379976
0 2 0.20378517242379976
0 2 -0.03307326586698826
0 2 -0.00033444921358650765
0 2 0.09150597080511258
0 2 0.0009253425677392942
[[ 0.00000000e+00 -4.96643883e-01  2.50004046e-01 -2.46638891e-01]
 [ 0.00000000e+00  0.00000000e+00 -2.50004043e-01 -2.46638891e-01]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  1.05947373e-09]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  

 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00]]
0 2 0.0003329321540625325
0 2 0.0330737508543352
0 2 -0.0009211460453265743
0 2 -0.09150739924696578
0 2 0.04579683962000971
0 2 0.045796838507075346
0 2 -0.07878454526909999
0 2 -0.07878454526909999
0 2 -0.04579683962000971
0 2 -0.045796838507075346
0 2 0.20378654894406567
0 2 0.20378654894406567
0 2 -0.033073749601249064
0 2 -0.0003329321252669845
0 2 0.09150739924696581
0 2 0.0009211460453265743
[[ 0.00000000e+00 -4.96659089e-01  2.50004009e-01 -2.46654143e-01]
 [ 0.00000000e+00  0.00000000e+00 -2.50004006e-01 -2.46654143e-01]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  1.00157809e-09]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00]]
0 2 0.0003328877418007787
0 2 0.033073765013365404
0 2 -0.0009210231935274879
0 2 -0.09150744106361271
0 2 0.04579685469542742
0 2 0.045796853584327446
0 2 -0.07878458610580678
0 2 -0.07878458610580678
0 2 -0.04579685469542742
0 2 -0.045796853584327446
0 2 0.20

0 2 0.04579731899825983
0 2 -0.07878584665620408
0 2 -0.07878584665620411
0 2 -0.04579732005397106
0 2 -0.04579731899825984
0 2 0.20378783319799507
0 2 0.20378783319799498
0 2 -0.03307420089136691
0 2 -0.0003315167792407064
0 2 0.09150873186338358
0 2 0.0009172309516625189
[[ 0.00000000e+00 -4.96673276e-01  2.50003974e-01 -2.46668371e-01]
 [ 0.00000000e+00  0.00000000e+00 -2.50003972e-01 -2.46668371e-01]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  9.49986535e-10]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00]]
0 2 0.0003314727704335358
0 2 0.03307421611908082
0 2 -0.0009171091404163807
0 2 -0.09150877332492129
0 2 0.045797335001963535
0 2 0.045797333947992264
0 2 -0.07878588714609135
0 2 -0.07878588714609133
0 2 -0.04579733500196353
0 2 -0.04579733394799225
0 2 0.20378787315601296
0 2 0.20378787315601296
0 2 -0.03307421493240644
0 2 -0.00033147274328367514
0 2 0.09150877332492133
0 2 0.0009171091404163807
[[ 0.00000000e+00 -4.96673717e-01  2.50003973e-01 -2.4

In [20]:
initial_ising = IsingModel()
sim_len = 20000
burn_in_len = 100
inter_burn_in = 10
num_runs = 100
num_spins = 4
H, J, model_mean, model_correlation = initial_ising.create_initial_conditions(num_spins, num_runs, sim_len, burn_in_len, inter_burn_in)

[-0.0054536  -0.01546477  0.00982367 -0.01101068] iniH
[[ 0.          0.0043651   0.00096497 -0.01863493]
 [ 0.          0.         -0.00082741 -0.00627001]
 [ 0.          0.          0.          0.00884622]
 [ 0.          0.          0.          0.        ]] iniJ
[-0.00457286 -0.01867337  0.00535678 -0.01033166] Mean Data
[0.01992961 0.02050408 0.02109502 0.02175645] Std Data
[[ 0.          0.00742714 -0.00052261 -0.01745729]
 [ 0.          0.          0.00348744 -0.00850251]
 [ 0.          0.          0.          0.01164824]
 [ 0.          0.          0.          0.        ]] Corr Data
[[0.         0.02082023 0.02261797 0.02213824]
 [0.         0.         0.02233936 0.02475849]
 [0.         0.         0.         0.02215851]
 [0.         0.         0.         0.        ]] Corr STD


In [4]:
s_ising.train_metropolis( max_epochs = 10000, simulation_len = 500, burn_in_len=25,  inter_burn_in=5)

Epoch 50 TotalParamVariation 0.01110526
[[ 0.         -0.30526316  0.2        -0.03157895]
 [ 0.          0.         -0.17894737 -0.03157895]
 [ 0.          0.          0.          0.09473684]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.24210526 -0.17894737  0.32631579  0.01052632] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 100 TotalParamVariation 0.01152632
[[ 0.         -0.41052632  0.2        -0.05263158]
 [ 0.          0.         -0.15789474 -0.11578947]
 [ 0.          0.          0.          0.07368421]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.11578947 -0.07368421  0.32631579  0.03157895] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 150 TotalParamVariation 0.01826316


Epoch 950 TotalParamVariation 0.00536842
[[ 0.         -0.55789474  0.17894737 -0.22105263]
 [ 0.          0.         -0.32631579 -0.17894737]
 [ 0.          0.          0.          0.01052632]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.30526316 -0.32631579  0.53684211  0.05263158] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 1000 TotalParamVariation 0.00721053
[[ 0.         -0.41052632  0.17894737 -0.28421053]
 [ 0.          0.         -0.01052632 -0.26315789]
 [ 0.          0.          0.         -0.01052632]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.13684211 -0.22105263  0.49473684  0.11578947] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 1050 TotalParamVariation 0.009157

Epoch 1850 TotalParamVariation 0.00684211
[[ 0.         -0.51578947  0.30526316 -0.28421053]
 [ 0.          0.         -0.07368421 -0.2       ]
 [ 0.          0.          0.         -0.13684211]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.36842105 -0.17894737  0.51578947  0.01052632] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 1900 TotalParamVariation 0.00831579
[[ 0.         -0.57894737  0.17894737 -0.13684211]
 [ 0.          0.         -0.22105263 -0.28421053]
 [ 0.          0.          0.         -0.11578947]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.22105263 -0.17894737  0.36842105 -0.15789474] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 1950 TotalParamVariation 0.01010

Epoch 2750 TotalParamVariation 0.00631579
[[ 0.         -0.64210526  0.32631579 -0.09473684]
 [ 0.          0.         -0.30526316 -0.17894737]
 [ 0.          0.          0.          0.03157895]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.28421053 -0.22105263  0.49473684  0.03157895] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 2800 TotalParamVariation 0.00984211
[[ 0.         -0.57894737  0.28421053 -0.24210526]
 [ 0.          0.         -0.28421053 -0.17894737]
 [ 0.          0.          0.         -0.2       ]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.13684211 -0.05263158  0.43157895 -0.17894737] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 2850 TotalParamVariation 0.00747

Epoch 3650 TotalParamVariation 0.00747368
[[ 0.         -0.30526316  0.2        -0.26315789]
 [ 0.          0.         -0.17894737 -0.43157895]
 [ 0.          0.          0.         -0.05263158]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.24210526 -0.26315789  0.45263158  0.11578947] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 3700 TotalParamVariation 0.00705263
[[ 0.         -0.49473684  0.30526316 -0.13684211]
 [ 0.          0.         -0.17894737 -0.36842105]
 [ 0.          0.          0.         -0.11578947]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.22105263 -0.30526316  0.36842105  0.01052632] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 3750 TotalParamVariation 0.00815

...

Epoch 6350 TotalParamVariation 0.007
[[ 0.         -0.53684211  0.15789474 -0.15789474]
 [ 0.          0.         -0.24210526 -0.30526316]
 [ 0.          0.          0.         -0.03157895]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.11578947 -0.32631579  0.57894737  0.09473684] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 6400 TotalParamVariation 0.00968421
[[ 0.         -0.43157895 -0.03157895 -0.15789474]
 [ 0.          0.         -0.15789474 -0.36842105]
 [ 0.          0.          0.         -0.01052632]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.17894737 -0.2         0.32631579 -0.01052632] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 6450 TotalParamVariation 0.00905263
[

Epoch 7250 TotalParamVariation 0.00615789
[[ 0.         -0.45263158  0.28421053 -0.41052632]
 [ 0.          0.         -0.2        -0.13684211]
 [ 0.          0.          0.         -0.03157895]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.17894737 -0.17894737  0.47368421 -0.01052632] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 7300 TotalParamVariation 0.00878947
[[ 0.         -0.36842105  0.36842105 -0.34736842]
 [ 0.          0.         -0.15789474 -0.28421053]
 [ 0.          0.          0.         -0.13684211]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.26315789 -0.17894737  0.47368421 -0.15789474] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 7350 TotalParamVariation 0.00678

Epoch 8150 TotalParamVariation 0.00378947
[[ 0.         -0.45263158  0.24210526 -0.26315789]
 [ 0.          0.         -0.2        -0.28421053]
 [ 0.          0.          0.         -0.01052632]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.28421053 -0.2         0.62105263 -0.01052632] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 8200 TotalParamVariation 0.00631579
[[ 0.         -0.49473684  0.24210526 -0.26315789]
 [ 0.          0.         -0.41052632 -0.2       ]
 [ 0.          0.          0.          0.03157895]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.22105263 -0.43157895  0.6         0.05263158] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 8250 TotalParamVariation 0.00873

Epoch 9050 TotalParamVariation 0.01473684
[[ 0.         -0.55789474  0.51578947 -0.15789474]
 [ 0.          0.         -0.53684211 -0.28421053]
 [ 0.          0.          0.          0.07368421]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.38947368 -0.49473684  0.53684211  0.24210526] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 9100 TotalParamVariation 0.01057895
[[ 0.         -0.64210526  0.32631579 -0.41052632]
 [ 0.          0.         -0.22105263  0.05263158]
 [ 0.          0.          0.         -0.03157895]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.17894737 -0.15789474  0.51578947 -0.13684211] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 9150 TotalParamVariation 0.00778

Epoch 9950 TotalParamVariation 0.01310526
[[ 0.         -0.45263158  0.05263158 -0.38947368]
 [ 0.          0.         -0.09473684 -0.11578947]
 [ 0.          0.          0.          0.05263158]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.43157895 -0.17894737  0.36842105 -0.2       ] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Epoch 9999 TotalParamVariation 0.005
[[ 0.         -0.49473684  0.2        -0.26315789]
 [ 0.          0.         -0.2        -0.24210526]
 [ 0.          0.          0.          0.11578947]
 [ 0.          0.          0.          0.        ]] Corr Model
[[ 0.   -0.5   0.25 -0.25]
 [ 0.    0.   -0.25 -0.25]
 [ 0.    0.    0.    0.  ]
 [ 0.    0.    0.    0.  ]] Corr Data
[ 0.32631579 -0.24210526  0.62105263 -0.05263158] Average Model
[ 0.25 -0.25  0.5   0.  ] Average Data

Final stats. TotalParamVariation 0.005
Tota

In [25]:
a = [0.9107870628157124, 0.9710475931636243, -0.9682787056576644, -1.0325613050491655, 1.0002218579424096, 1.0000854191038566, -1.0028838357897643, -1.0029590186436916, -1.0003863975670955, -1.0000656942225046, 1.127784980225538, 1.1276617774188478, -0.9709858494773228, -0.9103129982604652, 1.0323862030607138, 0.9680813132145235]

In [27]:
sum(a)

0.24962240227755228